# 🚲 MLflow via Delta Sharing: Training with AutoML

This notebook demonstrates how to train and register models in Unity Catalog from one workspace (Dev) and then use the shared artifacts in another workspace (Prod) for model inferencing.

Databricks provides a hosted MLflow Model Registry in Unity Catalog, fully compatible with the open-source MLflow Python client.  
Key benefits include:
- Centralized access control
- Full auditing and lineage tracking
- Cross-workspace model discovery and collaboration

**Dataset:** [Bike Sharing Dataset](https://archive.ics.uci.edu/dataset/275/bike+sharing+dataset)

---

## 📚 Workflow Overview

- Load the Bike Sharing dataset.
- Train a model using AutoML with hyperparameter tuning.
- Register the best-performing model to Unity Catalog (UC).
- Share the model via Delta Sharing to another workspace.
- Load the shared model in a second workspace and perform predictions.

---

## ⚙️ Requirements

- Databricks Runtime: **15.4 LTS ML** or later
- Unity Catalog enabled in both workspaces
- AutoML enabled

---

## Workspace A (Train + Register)

1. Trigger an AutoML experiment (including hyperparameter tuning).
2. Log the best model and experiment runs with MLflow.
3. Register the best model to UC Model Registry as:  
   `alexander_booth.default.bike_sharing_uc_model`
4. Share the registered model via Delta Sharing to Workspace B.

---

## Workspace B (Consume + Predict)

5. Accept the shared model via Unity Catalog UI or API.
6. Access the shared model using:  
   `models:/shared_catalog.shared_schema.bike_sharing_model`
7. Load the model and run batch predictions on new data.

---


## 🗂️ Unity Catalog Setup

Set the catalog and schema where the model will be registered.

You will need the following privileges:
- `USE CATALOG` on the target catalog
- `USE SCHEMA` and `CREATE MODEL` on the target schema

Update the catalog and schema below if necessary before proceeding.


In [0]:
# Catalog name where the model artifacts will be stored in Unity Catalog
CATALOG_NAME = "alexander_booth" 
SCHEMA_NAME = "default" # Schema (database) name within the catalog to organize model artifacts
TABLE_NAME = "bike_sharing_training_data"
MODEL_NAME = "bike_sharing_uc_model"

## 📊 Data Description

Dataset: [Bike Sharing Dataset (UCI ML Repository)](https://archive.ics.uci.edu/dataset/275/bike+sharing+dataset)

---

### 🔹 Features

| Column      | Description |
|:------------|:-------------|
| dteday      | Date |
| season      | Season (1: Spring, 2: Summer, 3: Fall, 4: Winter) |
| yr          | Year (0: 2011, 1: 2012) |
| mnth        | Month (1–12) |
| hr          | Hour of day (0–23) |
| holiday     | 1 if holiday, 0 otherwise |
| weekday     | Day of week (0 = Sunday) |
| workingday  | 1 if working day, 0 if weekend/holiday |
| weathersit  | Weather condition (1–4 scale) |
| temp        | Normalized temperature |
| atemp       | Normalized "feels like" temperature |
| hum         | Normalized humidity |
| windspeed   | Normalized wind speed |

---

### 🔹 Labels

| Column      | Description |
|:------------|:-------------|
| casual      | Count of casual users |
| registered  | Count of registered users |
| cnt         | Total rental count (casual + registered) |

---

### 🔹 Extra

| Column      | Description |
|:------------|:-------------|
| instant     | Record index (row ID) |

> Example:  
> Hour 0 on January 1, 2011 — 16 rentals recorded around midnight!


In [0]:
# Load the bike-sharing dataset from the specified CSV file into a Spark DataFrame.
# The dataset includes hourly bike rental data. The `header=True` option indicates that the first row contains column names,
# and `inferSchema=True` allows Spark to automatically infer data types for each column
bike_df = spark.read.csv(
    "/databricks-datasets/bikeSharing/data-001/hour.csv",
    header=True,
    inferSchema=True
)

# Print the schema of the loaded DataFrame to understand the structure and data types of its columns
print(bike_df.printSchema())
display(bike_df)

root
 |-- instant: integer (nullable = true)
 |-- dteday: date (nullable = true)
 |-- season: integer (nullable = true)
 |-- yr: integer (nullable = true)
 |-- mnth: integer (nullable = true)
 |-- hr: integer (nullable = true)
 |-- holiday: integer (nullable = true)
 |-- weekday: integer (nullable = true)
 |-- workingday: integer (nullable = true)
 |-- weathersit: integer (nullable = true)
 |-- temp: double (nullable = true)
 |-- atemp: double (nullable = true)
 |-- hum: double (nullable = true)
 |-- windspeed: double (nullable = true)
 |-- casual: integer (nullable = true)
 |-- registered: integer (nullable = true)
 |-- cnt: integer (nullable = true)

None


instant dteday season yr mnth hr holiday weekday workingday weathersit temp atemp hum windspeed casual registered cnt 1 2011-01-01 1 0 1 0 0 6 0 1 0.24 0.2879 0.81 0.0 3 13 16 2 2011-01-01 1 0 1 1 0 6 0 1 0.22 0.2727 0.8 0.0 8 32 40 3 2011-01-01 1 0 1 2 0 6 0 1 0.22 0.2727 0.8 0.0 5 27 32 4 2011-01-01 1 0 1 3 0 6 0 1 0.24 0.2879 0.75 0.0 3 10 13 5 2011-01-01 1 0 1 4 0 6 0 1 0.24 0.2879 0.75 0.0 0 1 1 6 2011-01-01 1 0 1 5 0 6 0 2 0.24 0.2576 0.75 0.0896 0 1 1 7 2011-01-01 1 0 1 6 0 6 0 1 0.22 0.2727 0.8 0.0 2 0 2 8 2011-01-01 1 0 1 7 0 6 0 1 0.2 0.2576 0.86 0.0 1 2 3 9 2011-01-01 1 0 1 8 0 6 0 1 0.24 0.2879 0.75 0.0 1 7 8 10 2011-01-01 1 0 1 9 0 6 0 1 0.32 0.3485 0.76 0.0 8 6 14 11 2011-01-01 1 0 1 10 0 6 0 1 0.38 0.3939 0.76 0.2537 12 24 36 12 2011-01-01 1 0 1 11 0 6 0 1 0.36 0.3333 0.81 0.2836 26 30 56 13 2011-01-01 1 0 1 12 0 6 0 1 0.42 0.4242 0.77 0.2836 29 55 84 14 2011-01-01 1 0 1 13 0 6 0 2 0.46 0.4545 0.72 0.2985 47 47 94 15 2011-01-01 1 0 1 14 0 6 0 2 0.46 0.4545 0.72 0.2836 35 71 106 16 2011-01-01 1 0 1 15 0 6 0 2 0.44 0.4394 0.77 0.2985 40 70 110 17 2011-01-01 1 0 1 16 0 6 0 2 0.42 0.4242 0.82 0.2985 41 52 93 18 2011-01-01 1 0 1 17 0 6 0 2 0.44 0.4394 0.82 0.2836 15 52 67 19 2011-01-01 1 0 1 18 0 6 0 3 0.42 0.4242 0.88 0.2537 9 26 35 20 2011-01-01 1 0 1 19 0 6 0 3 0.42 0.4242 0.88 0.2537 6 31 37 21 2011-01-01 1 0 1 20 0 6 0 2 0.4 0.4091 0.87 0.2537 11 25 36 22 2011-01-01 1 0 1 21 0 6 0 2 0.4 0.4091 0.87 0.194 3 31 34 23 2011-01-01 1 0 1 22 0 6 0 2 0.4 0.4091 0.94 0.2239 11 17 28 24 2011-01-01 1 0 1 23 0 6 0 2 0.46 0.4545 0.88 0.2985 15 24 39 25 2011-01-02 1 0 1 0 0 0 0 2 0.46 0.4545 0.88 0.2985 4 13 17 26 2011-01-02 1 0 1 1 0 0 0 2 0.44 0.4394 0.94 0.2537 1 16 17 27 2011-01-02 1 0 1 2 0 0 0 2 0.42 0.4242 1.0 0.2836 1 8 9 28 2011-01-02 1 0 1 3 0 0 0 2 0.46 0.4545 0.94 0.194 2 4 6 29 2011-01-02 1 0 1 4 0 0 0 2 0.46 0.4545 0.94 0.194 2 1 3 30 2011-01-02 1 0 1 6 0 0 0 3 0.42 0.4242 0.77 0.2985 0 2 2 31 2011-01-02 1 0 1 7 0 0 0 2 0.4 0.4091 0.76 0.194 0 1 1 32 2011-01-02 1 0 1 8 0 0 0 3 0.4 0.4091 0.71 0.2239 0 8 8 33 2011-01-02 1 0 1 9 0 0 0 2 0.38 0.3939 0.76 0.2239 1 19 20 34 2011-01-02 1 0 1 10 0 0 0 2 0.36 0.3485 0.81 0.2239 7 46 53 35 2011-01-02 1 0 1 11 0 0 0 2 0.36 0.3333 0.71 0.2537 16 54 70 36 2011-01-02 1 0 1 12 0 0 0 2 0.36 0.3333 0.66 0.2985 20 73 93 37 2011-01-02 1 0 1 13 0 0 0 2 0.36 0.3485 0.66 0.1343 11 64 75 38 2011-01-02 1 0 1 14 0 0 0 3 0.36 0.3485 0.76 0.194 4 55 59 39 2011-01-02 1 0 1 15 0 0 0 3 0.34 0.3333 0.81 0.1642 19 55 74 40 2011-01-02 1 0 1 16 0 0 0 3 0.34 0.3333 0.71 0.1642 9 67 76 41 2011-01-02 1 0 1 17 0 0 0 1 0.34 0.3333 0.57 0.194 7 58 65 42 2011-01-02 1 0 1 18 0 0 0 2 0.36 0.3333 0.46 0.3284 10 43 53 43 2011-01-02 1 0 1 19 0 0 0 1 0.32 0.2879 0.42 0.4478 1 29 30 44 2011-01-02 1 0 1 20 0 0 0 1 0.3 0.2727 0.39 0.3582 5 17 22 45 2011-01-02 1 0 1 21 0 0 0 1 0.26 0.2273 0.44 0.3284 11 20 31 46 2011-01-02 1 0 1 22 0 0 0 1 0.24 0.2121 0.44 0.2985 0 9 9 47 2011-01-02 1 0 1 23 0 0 0 1 0.22 0.2273 0.47 0.1642 0 8 8 48 2011-01-03 1 0 1 0 0 1 1 1 0.22 0.197 0.44 0.3582 0 5 5 49 2011-01-03 1 0 1 1 0 1 1 1 0.2 0.1667 0.44 0.4179 0 2 2 50 2011-01-03 1 0 1 4 0 1 1 1 0.16 0.1364 0.47 0.3881 0 1 1 51 2011-01-03 1 0 1 5 0 1 1 1 0.16 0.1364 0.47 0.2836 0 3 3 52 2011-01-03 1 0 1 6 0 1 1 1 0.14 0.1061 0.5 0.3881 0 30 30 53 2011-01-03 1 0 1 7 0 1 1 1 0.14 0.1364 0.5 0.194 1 63 64 54 2011-01-03 1 0 1 8 0 1 1 1 0.14 0.1212 0.5 0.2836 1 153 154 55 2011-01-03 1 0 1 9 0 1 1 1 0.16 0.1364 0.43 0.3881 7 81 88 56 2011-01-03 1 0 1 10 0 1 1 1 0.18 0.1667 0.43 0.2537 11 33 44 57 2011-01-03 1 0 1 11 0 1 1 1 0.2 0.1818 0.4 0.3284 10 41 51 58 2011-01-03 1 0 1 12 0 1 1 1 0.22 0.2121 0.35 0.2985 13 48 61 59 2011-01-03 1 0 1 13 0 1 1 1 0.24 0.2121 0.35 0.2836 8 53 61 60 2011-01-03 1 0 1 14 0 1 1 1 0.26 0.2424 0.3 0.2836 11 66 77 61 2011-01-03 1 0 1 15 0 1 1 1 0.26 0.2424 0.3 0.2537 14 58 72 62 2011-01-03 1 0 1 16 0 1 1 1 0.26 0.2424 0.3 0.2537 9 67 76 63 2011-01-03 1 0 1 17 0 1 1 1 0.24 0.2273 0.3 0.2239 11 146 157 64 2011-01-

In [0]:
# Step 2: Prepare data for training - Convert Spark DataFrame to Pandas DataFrame.

# Select only the relevant columns from the dataset that will be used for modeling
# These columns include features such as season, year, month, hour, weather conditions, and target variable (`cnt`)
selected_columns = ['season', 'yr', 'mnth', 'hr', 'holiday', 'weekday', 
                    'workingday', 'weathersit', 'temp', 'atemp', 'hum', 
                    'windspeed', 'cnt']

# Filter the DataFrame to include only the selected columns
bike_df = bike_df.select(selected_columns)
display(bike_df)

season yr mnth hr holiday weekday workingday weathersit temp atemp hum windspeed cnt 1 0 1 0 0 6 0 1 0.24 0.2879 0.81 0.0 16 1 0 1 1 0 6 0 1 0.22 0.2727 0.8 0.0 40 1 0 1 2 0 6 0 1 0.22 0.2727 0.8 0.0 32 1 0 1 3 0 6 0 1 0.24 0.2879 0.75 0.0 13 1 0 1 4 0 6 0 1 0.24 0.2879 0.75 0.0 1 1 0 1 5 0 6 0 2 0.24 0.2576 0.75 0.0896 1 1 0 1 6 0 6 0 1 0.22 0.2727 0.8 0.0 2 1 0 1 7 0 6 0 1 0.2 0.2576 0.86 0.0 3 1 0 1 8 0 6 0 1 0.24 0.2879 0.75 0.0 8 1 0 1 9 0 6 0 1 0.32 0.3485 0.76 0.0 14 1 0 1 10 0 6 0 1 0.38 0.3939 0.76 0.2537 36 1 0 1 11 0 6 0 1 0.36 0.3333 0.81 0.2836 56 1 0 1 12 0 6 0 1 0.42 0.4242 0.77 0.2836 84 1 0 1 13 0 6 0 2 0.46 0.4545 0.72 0.2985 94 1 0 1 14 0 6 0 2 0.46 0.4545 0.72 0.2836 106 1 0 1 15 0 6 0 2 0.44 0.4394 0.77 0.2985 110 1 0 1 16 0 6 0 2 0.42 0.4242 0.82 0.2985 93 1 0 1 17 0 6 0 2 0.44 0.4394 0.82 0.2836 67 1 0 1 18 0 6 0 3 0.42 0.4242 0.88 0.2537 35 1 0 1 19 0 6 0 3 0.42 0.4242 0.88 0.2537 37 1 0 1 20 0 6 0 2 0.4 0.4091 0.87 0.2537 36 1 0 1 21 0 6 0 2 0.4 0.4091 0.87 0.194 34 1 0 1 22 0 6 0 2 0.4 0.4091 0.94 0.2239 28 1 0 1 23 0 6 0 2 0.46 0.4545 0.88 0.2985 39 1 0 1 0 0 0 0 2 0.46 0.4545 0.88 0.2985 17 1 0 1 1 0 0 0 2 0.44 0.4394 0.94 0.2537 17 1 0 1 2 0 0 0 2 0.42 0.4242 1.0 0.2836 9 1 0 1 3 0 0 0 2 0.46 0.4545 0.94 0.194 6 1 0 1 4 0 0 0 2 0.46 0.4545 0.94 0.194 3 1 0 1 6 0 0 0 3 0.42 0.4242 0.77 0.2985 2 1 0 1 7 0 0 0 2 0.4 0.4091 0.76 0.194 1 1 0 1 8 0 0 0 3 0.4 0.4091 0.71 0.2239 8 1 0 1 9 0 0 0 2 0.38 0.3939 0.76 0.2239 20 1 0 1 10 0 0 0 2 0.36 0.3485 0.81 0.2239 53 1 0 1 11 0 0 0 2 0.36 0.3333 0.71 0.2537 70 1 0 1 12 0 0 0 2 0.36 0.3333 0.66 0.2985 93 1 0 1 13 0 0 0 2 0.36 0.3485 0.66 0.1343 75 1 0 1 14 0 0 0 3 0.36 0.3485 0.76 0.194 59 1 0 1 15 0 0 0 3 0.34 0.3333 0.81 0.1642 74 1 0 1 16 0 0 0 3 0.34 0.3333 0.71 0.1642 76 1 0 1 17 0 0 0 1 0.34 0.3333 0.57 0.194 65 1 0 1 18 0 0 0 2 0.36 0.3333 0.46 0.3284 53 1 0 1 19 0 0 0 1 0.32 0.2879 0.42 0.4478 30 1 0 1 20 0 0 0 1 0.3 0.2727 0.39 0.3582 22 1 0 1 21 0 0 0 1 0.26 0.2273 0.44 0.3284 31 1 0 1 22 0 0 0 1 0.24 0.2121 0.44 0.2985 9 1 0 1 23 0 0 0 1 0.22 0.2273 0.47 0.1642 8 1 0 1 0 0 1 1 1 0.22 0.197 0.44 0.3582 5 1 0 1 1 0 1 1 1 0.2 0.1667 0.44 0.4179 2 1 0 1 4 0 1 1 1 0.16 0.1364 0.47 0.3881 1 1 0 1 5 0 1 1 1 0.16 0.1364 0.47 0.2836 3 1 0 1 6 0 1 1 1 0.14 0.1061 0.5 0.3881 30 1 0 1 7 0 1 1 1 0.14 0.1364 0.5 0.194 64 1 0 1 8 0 1 1 1 0.14 0.1212 0.5 0.2836 154 1 0 1 9 0 1 1 1 0.16 0.1364 0.43 0.3881 88 1 0 1 10 0 1 1 1 0.18 0.1667 0.43 0.2537 44 1 0 1 11 0 1 1 1 0.2 0.1818 0.4 0.3284 51 1 0 1 12 0 1 1 1 0.22 0.2121 0.35 0.2985 61 1 0 1 13 0 1 1 1 0.24 0.2121 0.35 0.2836 61 1 0 1 14 0 1 1 1 0.26 0.2424 0.3 0.2836 77 1 0 1 15 0 1 1 1 0.26 0.2424 0.3 0.2537 72 1 0 1 16 0 1 1 1 0.26 0.2424 0.3 0.2537 76 1 0 1 17 0 1 1 1 0.24 0.2273 0.3 0.2239 157 1 0 1 18 0 1 1 1 0.24 0.2576 0.32 0.1045 157 1 0 1 19 0 1 1 1 0.2 0.2576 0.47 0.0 110 1 0 1 20 0 1 1 1 0.2 0.2273 0.47 0.1045 52 1 0 1 21 0 1 1 1 0.18 0.197 0.64 0.1343 52 1 0 1 22 0 1 1 1 0.14 0.1515 0.69 0.1343 20 1 0 1 23 0 1 1 1 0.18 0.2121 0.55 0.1045 12 1 0 1 0 0 2 1 1 0.16 0.1818 0.55 0.1045 5 1 0 1 1 0 2 1 1 0.16 0.1818 0.59 0.1045 2 1 0 1 2 0 2 1 1 0.14 0.1515 0.63 0.1343 1 1 0 1 4 0 2 1 1 0.14 0.1818 0.63 0.0896 2 1 0 1 5 0 2 1 1 0.12 0.1515 0.68 0.1045 4 1 0 1 6 0 2 1 1 0.12 0.1515 0.74 0.1045 36 1 0 1 7 0 2 1 1 0.12 0.1515 0.74 0.1343 94 1 0 1 8 0 2 1 1 0.14 0.1515 0.69 0.1642 179 1 0 1 9 0 2 1 1 0.16 0.1515 0.64 0.2239 100 1 0 1 10 0 2 1 2 0.16 0.1364 0.69 0.3284 42 1 0 1 11 0 2 1 1 0.22 0.2121 0.51 0.2985 57 1 0 1 12 0 2 1 1 0.22 0.2273 0.51 0.1642 78 1 0 1 13 0 2 1 1 0.24 0.2273 0.56 0.194 97 1 0 1 14 0 2 1 1 0.26 0.2576 0.52 0.2239 63 1 0 1 15 0 2 1 1 0.28 0.2727 0.52 0.2537 65 1 0 1 16 0 2 1 1 0.3 0.2879 0.49 0.2537 83 1 0 1 17 0 2 1 1 0.28 0.2727 0.48 0.2239 212 1 0 1 18 0 2 1 1 0.26 0.2576 0.48 0.194 182 1 0 1 19 0 2 1 1 0.24 0.2576 0.48 0.1045 112 1 0 1 20 0 2 1 1 0.24 0.2576 0.48 0.1045 54 1 0 1 21 0 2 1 1 0.22 0.2727 0.64 0.0 48 1 0 1 22 0 2 1 1 0.22 0.2576 0.64 0.0896 35 1 0 1 23 0 2 1 1 0.2 0.227

In [0]:
# Save it as a table
bike_df.write.mode("overwrite").saveAsTable(f"{CATALOG_NAME}.{SCHEMA_NAME}.{TABLE_NAME}")

## Machine Learning

In [0]:
# 1. Import packages
import databricks.automl
from mlflow import register_model
import mlflow

# Set the MLflow registry URI to use Databricks Unity Catalog (UC) for model registry management
mlflow.set_registry_uri("databricks-uc")

In [0]:
# 2. Define configs
input_table = f"{CATALOG_NAME}.{SCHEMA_NAME}.{TABLE_NAME}"
target_col = "cnt"
uc_model_name = f"{CATALOG_NAME}.{SCHEMA_NAME}.{MODEL_NAME}"
experiment_name = "bike_sharing_uc"

# 3. Launch AutoML
summary = databricks.automl.regress(
    dataset = input_table,
    target_col = target_col,
    timeout_minutes = 5,
    primary_metric = "rmse",
    experiment_name = experiment_name
)

print(summary)

2025/04/18 19:15:02 INFO databricks.automl.client.manager: AutoML will optimize for root mean squared error metric, which is tracked as val_root_mean_squared_error in the MLflow experiment.
2025/04/18 19:15:04 INFO databricks.automl.client.manager: MLflow Experiment ID: 2674917388788605
2025/04/18 19:15:04 INFO databricks.automl.client.manager: MLflow Experiment: https://e2-demo-field-eng.cloud.databricks.com/?o=1444828305810485#mlflow/experiments/2674917388788605


🏃 View run masked-sow-621 at: https://e2-demo-field-eng.cloud.databricks.com/ml/experiments/2674917388788605/runs/7a5b6f89946248ae830079aa8e7139f2
🧪 View experiment at: https://e2-demo-field-eng.cloud.databricks.com/ml/experiments/2674917388788605


2025/04/18 19:17:21 INFO databricks.automl.client.manager: Data exploration notebook: https://e2-demo-field-eng.cloud.databricks.com/?o=1444828305810485#notebook/2674917388788641
2025/04/18 19:20:58 INFO databricks.automl.client.manager: AutoML experiment completed successfully.


For exploratory data analysis, open the data exploration notebook 
 To view the best performing model, open the best trial notebook 
 To view details about all trials, navigate to the MLflow experiment 
 Metrics for the best trial: 
 
 <!-- class inlined from webapp/web/js/templates/iframeSandbox.css -->
 
 
 
 
 
 Train 
 Validation 
 Test 
 
 
 
 
 
 root_mean_squared_error 
 36.710 
 44.281 
 41.954 
 
 

 
 mean_squared_error 
 1347.600 
 1960.771 
 1760.157 
 
 

 
 example_count 
 10441.000 
 3403.000 
 3535.000 
 
 

 
 r2_score 
 0.959 
 0.942 
 0.947 
 
 

 
 sum_on_target 
 1.971133e+06 
 651061.000 
 670485.000 
 
 

 
 score 
 0.959 
 0.942 
 0.947 
 
 

 
 mean_absolute_error 
 24.045 
 28.664 
 27.583 
 
 

 
 mean_on_target 
 188.788 
 191.320 
 189.670 
 
 

 
 max_error 
 381.302 
 361.703 
 386.103 
 
 

 
 mean_absolute_percentage_error 
 0.499 
 0.531 
 0.574

Overall summary:
	Experiment ID: 2674917388788605
	Number of trials: 4
	Evaluation metric distribution: min: 264.298, median: 91.804, max: 44.281
	Semantic type conversions: {'categorical': ['season', 'yr', 'mnth', 'holiday', 'weekday', 'workingday', 'weathersit']}
Best trial:

	Model: Pipeline
	Model path: dbfs:/databricks/mlflow-tracking/2674917388788605/c8059d59c6624144a5020db3017da1a8/artifacts/model
	Preprocessors: [('boolean', Pipeline(steps=[('cast_type',
	         FunctionTransformer(func=<function <lambda> at 0x7fd7609d9080>)),
	        ('imputers',
	         ColumnTransformer(remainder='passthrough', transformers=[])),
	        ('onehot',
	         OneHotEncoder(drop='first', handle_unknown='ignore'))]), ['holiday', 'yr', 'workingday']), ('numerical', Pipeline(steps=[('converter',
	         FunctionTransformer(func=<function <lambda> at 0x7fd7609d9300>)),
	        ('imputers',
	         ColumnTransformer(transformers=[('impute_mean',
	                                         

In [0]:
# 4. Best trial info
best_run_id = summary.best_trial.mlflow_run_id
best_model_uri = f"runs:/{best_run_id}/model"

print(f"Best Run ID: {best_run_id}")
print(f"Best Model URI: {best_model_uri}")

# 5. Register the best model into UC
registered_model = mlflow.register_model(
    model_uri = best_model_uri,
    name = uc_model_name
)

print(f"Registered Model Version: {registered_model.version}")

Best Run ID: c8059d59c6624144a5020db3017da1a8
Best Model URI: runs:/c8059d59c6624144a5020db3017da1a8/model


Successfully registered model 'alexander_booth.default.bike_sharing_uc_model'.


Uploading artifacts:   0%|          | 0/11 [00:00<?, ?it/s]

Registered Model Version: 1


Created version '1' of model 'alexander_booth.default.bike_sharing_uc_model'.


## ✅ Next Steps

Now that the best model is trained and registered, the next steps are:

1. **Alias the model to "prod"**  
   - Promote the registered model version to the "prod" alias.
   - This allows easy future access without hardcoding specific model versions.

2. **Add the model to a Delta Sharing share**  
   - Enable external consumers (or other workspaces) to access the model.
   - Share the model artifact by adding it to an existing Delta Share.

Both of these steps are available through the UI; however, we are presenting them programmatically to provide a complete, end-to-end example.

In [0]:
# Initialize MLflow client
client = mlflow.MlflowClient()

# Set alias "staging" to the newly registered model version
client.set_registered_model_alias(
    name = uc_model_name,                       # Same model registered
    alias = "staging",
    version = registered_model.version          # Version registered
)

In [0]:
%sql
-- Create a new Delta Sharing share
CREATE SHARE abooth_bike_sharing_model_share
COMMENT "Share for production ML models.";


info_name info_value share_name abooth_bike_sharing_model_share owner alexander.booth@databricks.com created_at 2025-04-18 19:35:51.558 created_by alexander.booth@databricks.com updated_at 2025-04-18 19:35:51.558 updated_by alexander.booth@databricks.com comment Share for production ML models.

In [0]:
%sql
-- Add a recipient. Replace the recipient name with your own. Recipients can be created via SQL or in the UI.
GRANT SELECT ON SHARE abooth_bike_sharing_model_share TO RECIPIENT `xxxxxxxxxxxx`;


In [0]:
%sql
-- Add model to the Delta Sharing share
ALTER SHARE abooth_bike_sharing_model_share
ADD MODEL alexander_booth.default.bike_sharing_uc_model;

## 🚀 Pivot to Inference Demo

Now that the model has been trained, registered, and shared through Delta Sharing, we will pivot to a second workspace and notebook to demonstrate inference.

In the next section:
- We will simulate how an external consumer (another workspace or partner) would access the shared model.
- We will load the model directly from the Delta Sharing share.
- We will perform batch inference using the shared model on new data.

This approach demonstrates how Delta Sharing enables cross-workspace, cross-cloud model collaboration without manual exports.
